In [22]:
import requests
import re
import json
import sqlalchemy as db


In [23]:
engine = db.create_engine("sqlite:///donnees_sncf.db")
connection = engine.connect()

with engine.connect() as con:
    con.execute("DROP TABLE sncf_gare")

metadata = db.MetaData()

sncf_gare_table = db.Table("sncf_gare", metadata,
             db.Column('uic_code',db.String(),primary_key=True),
             db.Column('nom_gare',db.String()),
             db.Column('latitude',db.String()),
             db.Column('longitude', db.String()),
    
             db.Column('numero_dep',db.String()),
             
             )

metadata.create_all(engine)


In [24]:
url = "https://ressources.data.sncf.com/api/records/1.0/search/?dataset=referentiel-gares-voyageurs&facet=longitude_entreeprincipale_wgs84&facet=latitude_entreeprincipale_wgs84&facet=uic_code&facet=gare_alias_libelle_noncontraint&facet=departement_numero&rows=-1"
data = requests.get(url).json()
print(data)
for gare in data["records"]:
    uic_code=gare["fields"]["uic_code"]
    nom_gare=gare["fields"]["gare_alias_libelle_noncontraint"]
    try :
        latitude=gare["fields"]["latitude_entreeprincipale_wgs84"]
    except:
        latitude="None"
    try :
        longitude=gare["fields"]["longitude_entreeprincipale_wgs84"]
    except:
        longitude="None"
    try:
        numero_dep=gare["fields"]["departement_numero"]
    except:
        numero_dep="None"
    with engine.connect() as con:
                insertTable = "INSERT INTO sncf_gare (uic_code, nom_gare, latitude, longitude,numero_dep) VALUES (:uic_code, :nom_gare, :latitude, :longitude, :numero_dep)"
                params = {"uic_code":uic_code, "nom_gare":nom_gare, "latitude":latitude, "longitude":longitude, "numero_dep":numero_dep}
                statement = db.text(insertTable)
                try:
                    con.execute(statement,params)
                except:
                    continue

{'nhits': 3213, 'parameters': {'dataset': 'referentiel-gares-voyageurs', 'rows': 10000, 'start': 0, 'facet': ['longitude_entreeprincipale_wgs84', 'latitude_entreeprincipale_wgs84', 'uic_code', 'gare_alias_libelle_noncontraint', 'departement_numero'], 'format': 'json', 'timezone': 'UTC'}, 'records': [{'datasetid': 'referentiel-gares-voyageurs', 'recordid': 'e77fd98fa7ed624f66685cdd7c265fba232b1c35', 'fields': {'niveauservice_libelle': 1, 'wgs_84': [42.4199665, 1.9771166], 'tvs': 'OSA', 'gare_alias_libelle_noncontraint': 'Osséja', 'commune_libellemin': 'Osséja', 'tvss': '[{"TVS_Code": "OSA"}]', 'gare_alias_libelle_fronton': 'Osséja', 'commune_code': '130', 'uic_code': '0087784868', 'rg_libelle': 'GARES C LANGUEDOC ROUSSILLON', 'gare': '{"DRG_ON": true, "Etrangere_ON": false, "NbPltf": 1, "Alias_Libelle_NonContraint": "Osséja", "Alias_Libelle_Fronton": "Osséja", "AgenceGC_Libelle": "DRG Occitanie Sud", "RegionSNCF_Libelle": "REGION LANGUEDOC-ROUSSILLON", "UG_Libelle": "UG Est Occitanie", 